# Whats the Cause of your Power Outage?

**Name(s)**: Kaii Bijlani, Ketan Mittal

**Website Link**: https://k1mittal.github.io/Causes_of_Power_Outages/

In [549]:
import pandas as pd
import numpy as np
from pathlib import Path
import scipy    
import folium
from folium.plugins import HeatMap
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder, StandardScaler, Binarizer, FunctionTransformer
from sklearn.compose import ColumnTransformer
from sklearn.metrics import f1_score

import plotly.express as px
pd.options.plotting.backend = 'plotly'

from dsc80_utils import * # Feel free to uncomment and use this.

## Step 1: Introduction

### Interesting Questions:
- How does the cause of the power outages indicate other factors, for example, does whether related power outages result in more people having no power? Can we predict the cause of power outages?
- Is there a correlation between the time and other factors, do power outages happen in one month specifically? Has the number of power outages decreased over time? Can we predict when the next power outage is using a time series prediction?
- Can we predict the number of people affected by a power outage given certain factors? Are the number of people affected by power outages correlated to other factors?
- Can we predict the duration of power outages given certain factors? How are the duration of power outages correlated to other factors?

### Our Choice:
We decided to answer the first bullet point, which is what aspects of power outage are related to each category of cause. 

## Step 2: Data Cleaning and Exploratory Data Analysis

In [550]:
pd.set_option('display.max_columns', None)

In [551]:
# Data Init and Cleanin
raw_data = pd.read_excel(Path('.\outage.xlsx'))
raw_data.columns = [f'{raw_data.columns[i]}' for i in range(len(raw_data.columns))]
raw_data = raw_data.iloc[1:, 1:].loc[:, ['OBS', 'YEAR', 'MONTH', 'U.S._STATE', 'NERC.REGION', 'CLIMATE.REGION', 'ANOMALY.LEVEL', 'OUTAGE.START.DATE', 'OUTAGE.START.TIME', 'OUTAGE.RESTORATION.DATE', 'OUTAGE.RESTORATION.TIME', 'CAUSE.CATEGORY', 'CLIMATE.CATEGORY', 'CAUSE.CATEGORY.DETAIL', 'OUTAGE.DURATION', 'DEMAND.LOSS.MW', 'CUSTOMERS.AFFECTED', 'TOTAL.PRICE', 'TOTAL.SALES', 'TOTAL.CUSTOMERS', 'TOTAL.REALGSP']]


<>:2: SyntaxWarning:

invalid escape sequence '\o'

<>:2: SyntaxWarning:

invalid escape sequence '\o'

C:\Users\Kaii Bijlani\AppData\Local\Temp\ipykernel_73880\3665842156.py:2: SyntaxWarning:

invalid escape sequence '\o'



Below we display the only missing values for outage start dates. Note how there are only 9 entries, and each of these entries also have missing relevant features. Therefore, imputation is not something of interest in this case and we can simply drop these values

In [552]:
raw_data = raw_data.dropna(subset = ['OUTAGE.START.DATE', 'OUTAGE.START.TIME', 'OUTAGE.RESTORATION.DATE', 'OUTAGE.RESTORATION.TIME'], how = 'any')

raw_data['OUTAGE.START'] = pd.to_datetime(
    raw_data['OUTAGE.START.DATE'].astype(str) + ' ' + raw_data['OUTAGE.START.TIME'].astype(str)
)

raw_data['OUTAGE.END'] = pd.to_datetime(
    raw_data['OUTAGE.RESTORATION.DATE'].astype(str) + ' ' + raw_data['OUTAGE.RESTORATION.TIME'].astype(str)
)
raw_data = raw_data.drop(columns = ['OUTAGE.START.DATE', 'OUTAGE.START.TIME', 'OUTAGE.RESTORATION.DATE', 'OUTAGE.RESTORATION.TIME'])

raw_data['OUTAGE.START'].isna().sum()

C:\Users\Kaii Bijlani\AppData\Local\Temp\ipykernel_73880\2858319401.py:3: UserWarning:

Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.

C:\Users\Kaii Bijlani\AppData\Local\Temp\ipykernel_73880\2858319401.py:7: UserWarning:

Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.



np.int64(0)

#### Adding Seasons using Binning

In [553]:
seasons = {'(0, 1]': 'Winter', '(1, 4]': 'Spring', '(4, 7]': 'Summer', '(7, 10]': 'Fall', '(10, 12]': 'Winter'}

raw_data['SEASONAL.BINS'] = pd.cut(raw_data['MONTH'], bins = [0, 1, 4, 7, 10, 12])
raw_data['SEASONAL.BINS'] = raw_data['SEASONAL.BINS'].astype(str).map(seasons)
raw_data

OBS    YEAR  MONTH            U.S._STATE NERC.REGION  \
1        1.0  2011.0    7.0             Minnesota         MRO   
2        2.0  2014.0    5.0             Minnesota         MRO   
3        3.0  2010.0   10.0             Minnesota         MRO   
4        4.0  2012.0    6.0             Minnesota         MRO   
5        5.0  2015.0    7.0             Minnesota         MRO   
6        6.0  2010.0   11.0             Minnesota         MRO   
7        7.0  2010.0    7.0             Minnesota         MRO   
8        8.0  2005.0    6.0             Minnesota         MRO   
9        9.0  2015.0    3.0             Minnesota         MRO   
10      10.0  2013.0    6.0             Minnesota         MRO   
11      11.0  2013.0    6.0             Minnesota         MRO   
12      12.0  2005.0    9.0             Minnesota         MRO   
13      13.0  2011.0    7.0             Minnesota         MRO   
14      14.0  2011.0    5.0             Minnesota         MRO   
15      15.0  2014.0    6.0             Minnesota         MRO   
16      16.0  2015.0    6.0             Tennessee        SERC   
17      17.0  2012.0    8.0             Tennessee        SERC   
18      18.0  2015.0    6.0             Tennessee        SERC   
19      19.0  2011.0    4.0             Tennessee        SERC   
20      20.0  2008.0    2.0             Tennessee        SERC   
21      21.0  2015.0    1.0             Tennessee        SERC   
22      22.0  2012.0    7.0             Tennessee        SERC   
24      24.0  2013.0    4.0             Tennessee        SERC   
25      25.0  2014.0    1.0             Tennessee        SERC   
26      26.0  2009.0    7.0             Tennessee        SERC   
27      27.0  2011.0    6.0             Tennessee        SERC   
28      28.0  2011.0    4.0             Tennessee        SERC   
29      29.0  2014.0    6.0             Tennessee        SERC   
30      30.0  2012.0    6.0             Tennessee        SERC   
31      31.0  2014.0    6.0             Tennessee        SERC   
32      32.0  2011.0    4.0             Tennessee        SERC   
33      33.0  2015.0    5.0             Tennessee        SERC   
34      34.0  2015.0    2.0             Tennessee        SERC   
35      35.0  2014.0    6.0             Tennessee        SERC   
36      36.0  2011.0    4.0             Tennessee        SERC   
38      38.0  2014.0    1.0             Tennessee        SERC   
39      39.0  2015.0    3.0             Tennessee        SERC   
40      40.0  2013.0    1.0             Tennessee        SERC   
41      41.0  2011.0    4.0             Tennessee        SERC   
42      42.0  2009.0    6.0             Tennessee        SERC   
43      43.0  2014.0    3.0             Tennessee        SERC   
44      44.0  2014.0    1.0             Tennessee        SERC   
45      45.0  2011.0    4.0             Tennessee        SERC   
46      46.0  2014.0    6.0             Tennessee        SERC   
47      47.0  2014.0    1.0             Tennessee        SERC   
49      49.0  2009.0    1.0             Tennessee        SERC   
51      51.0  2014.0    1.0             Wisconsin         MRO   
52      52.0  2005.0   11.0             Wisconsin         RFC   
53      53.0  2013.0    8.0             Wisconsin         MRO   
54      54.0  2014.0    1.0             Wisconsin         RFC   
55      55.0  2014.0    4.0             Wisconsin         MRO   
56      56.0  2003.0    7.0             Wisconsin         RFC   
57      57.0  2014.0    1.0             Wisconsin         MRO   
58      58.0  2016.0    1.0             Wisconsin         MRO   
59      59.0  2005.0    9.0             Wisconsin         RFC   
60      60.0  2010.0    8.0             Wisconsin         MRO   
61      61.0  2010.0   10.0             Wisconsin         MRO   
62      62.0  2003.0    4.0             Wisconsin         MRO   
63      63.0  2014.0    1.0             Wisconsin         MRO   
64      64.0  2014.0    3.0             Wisconsin         MRO   
65      65.0  2014.0    6.0             Wisc

#### Simple Handling of NaN Values

In [554]:
raw_data.loc[raw_data['CUSTOMERS.AFFECTED'] == 0, 'CUSTOMERS.AFFECTED'] = np.nan
raw_data.loc[raw_data['OUTAGE.DURATION'] == 0, 'OUTAGE.DURATION'] = np.nan


### EDA

In [555]:
cause_pdf = px.histogram(raw_data, x = 'CAUSE.CATEGORY', title = 'Distributions of Observations by Cause', histnorm = 'probability density')
cause_pdf.update_layout(xaxis_title = 'Cause', yaxis_title = 'Frequency', legend_title_text = 'Climate Category', showlegend = True)
cause_pdf.show()

In [556]:
states_url = f'https://raw.githubusercontent.com/python-visualization/folium/main/examples/data/us-states.json'

states_data = raw_data['U.S._STATE'].value_counts().reset_index(drop = False)
states_data

U.S._STATE  count
0             California    198
1                  Texas    122
2               Michigan     95
3             Washington     89
4               New York     70
5               Maryland     58
6           Pennsylvania     57
7                Florida     45
8               Illinois     44
9                   Ohio     42
10               Indiana     42
11                  Utah     41
12              Delaware     40
13        North Carolina     39
14             Louisiana     38
15              Virginia     36
16            New Jersey     32
17             Tennessee     31
18                Oregon     25
19               Arizona     25
20              Arkansas     25
21              Oklahoma     22
22             Wisconsin     19
23         Massachusetts     18
24                 Maine     18
25           Connecticut     18
26               Georgia     17
27             Minnesota     15
28              Missouri     15
29              Colorado     14
30         New Hampshire     14
31              Kentucky     13
32  District of Columbia     10
33               Vermont      9
34                 Idaho      8
35        South Carolina      8
36            New Mexico      8
37                  Iowa      8
38                Kansas      7
39                Nevada      7
40               Wyoming      6
41               Alabama      5
42                Hawaii      5
43         West Virginia      4
44           Mississippi      4
45              Nebraska      4
46               Montana      3
47          South Dakota      2
48          North Dakota      1

In [557]:

m = folium.Map(location=[37.0902, -95.7129], zoom_start=4) # Centered on the US
folium.Choropleth(
    geo_data=states_url, 
    name='State Frequency',
    data=states_data, 
    columns=['U.S._STATE', 'count'],  # Replace 'state' and 'frequency' with your column names
    key_on='feature.properties.name', 
    fill_color='YlGn', 
    fill_opacity=0.7, 
    line_opacity=0.2, 
    legend_name='Frequency'
).add_to(m)
m

In [558]:
raw_data

OBS    YEAR  MONTH            U.S._STATE NERC.REGION  \
1        1.0  2011.0    7.0             Minnesota         MRO   
2        2.0  2014.0    5.0             Minnesota         MRO   
3        3.0  2010.0   10.0             Minnesota         MRO   
4        4.0  2012.0    6.0             Minnesota         MRO   
5        5.0  2015.0    7.0             Minnesota         MRO   
6        6.0  2010.0   11.0             Minnesota         MRO   
7        7.0  2010.0    7.0             Minnesota         MRO   
8        8.0  2005.0    6.0             Minnesota         MRO   
9        9.0  2015.0    3.0             Minnesota         MRO   
10      10.0  2013.0    6.0             Minnesota         MRO   
11      11.0  2013.0    6.0             Minnesota         MRO   
12      12.0  2005.0    9.0             Minnesota         MRO   
13      13.0  2011.0    7.0             Minnesota         MRO   
14      14.0  2011.0    5.0             Minnesota         MRO   
15      15.0  2014.0    6.0             Minnesota         MRO   
16      16.0  2015.0    6.0             Tennessee        SERC   
17      17.0  2012.0    8.0             Tennessee        SERC   
18      18.0  2015.0    6.0             Tennessee        SERC   
19      19.0  2011.0    4.0             Tennessee        SERC   
20      20.0  2008.0    2.0             Tennessee        SERC   
21      21.0  2015.0    1.0             Tennessee        SERC   
22      22.0  2012.0    7.0             Tennessee        SERC   
24      24.0  2013.0    4.0             Tennessee        SERC   
25      25.0  2014.0    1.0             Tennessee        SERC   
26      26.0  2009.0    7.0             Tennessee        SERC   
27      27.0  2011.0    6.0             Tennessee        SERC   
28      28.0  2011.0    4.0             Tennessee        SERC   
29      29.0  2014.0    6.0             Tennessee        SERC   
30      30.0  2012.0    6.0             Tennessee        SERC   
31      31.0  2014.0    6.0             Tennessee        SERC   
32      32.0  2011.0    4.0             Tennessee        SERC   
33      33.0  2015.0    5.0             Tennessee        SERC   
34      34.0  2015.0    2.0             Tennessee        SERC   
35      35.0  2014.0    6.0             Tennessee        SERC   
36      36.0  2011.0    4.0             Tennessee        SERC   
38      38.0  2014.0    1.0             Tennessee        SERC   
39      39.0  2015.0    3.0             Tennessee        SERC   
40      40.0  2013.0    1.0             Tennessee        SERC   
41      41.0  2011.0    4.0             Tennessee        SERC   
42      42.0  2009.0    6.0             Tennessee        SERC   
43      43.0  2014.0    3.0             Tennessee        SERC   
44      44.0  2014.0    1.0             Tennessee        SERC   
45      45.0  2011.0    4.0             Tennessee        SERC   
46      46.0  2014.0    6.0             Tennessee        SERC   
47      47.0  2014.0    1.0             Tennessee        SERC   
49      49.0  2009.0    1.0             Tennessee        SERC   
51      51.0  2014.0    1.0             Wisconsin         MRO   
52      52.0  2005.0   11.0             Wisconsin         RFC   
53      53.0  2013.0    8.0             Wisconsin         MRO   
54      54.0  2014.0    1.0             Wisconsin         RFC   
55      55.0  2014.0    4.0             Wisconsin         MRO   
56      56.0  2003.0    7.0             Wisconsin         RFC   
57      57.0  2014.0    1.0             Wisconsin         MRO   
58      58.0  2016.0    1.0             Wisconsin         MRO   
59      59.0  2005.0    9.0             Wisconsin         RFC   
60      60.0  2010.0    8.0             Wisconsin         MRO   
61      61.0  2010.0   10.0             Wisconsin         MRO   
62      62.0  2003.0    4.0             Wisconsin         MRO   
63      63.0  2014.0    1.0             Wisconsin         MRO   
64      64.0  2014.0    3.0             Wisconsin         MRO   
65      65.0  2014.0    6.0             Wisc

### Bivariate Analysis

In [559]:
duration_customers_plt = px.violin(raw_data, x = 'SEASONAL.BINS', y = 'ANOMALY.LEVEL')
duration_customers_plt.show()

In [560]:
px.scatter(raw_data, x = 'CLIMATE.REGION', y = 'OUTAGE.DURATION')

In [561]:
price_climate_cause = raw_data.pivot_table(index = 'CAUSE.CATEGORY', columns = 'CLIMATE.REGION', values = 'TOTAL.PRICE', aggfunc = 'mean')
price_climate_cause

CLIMATE.REGION                Central East North Central Northeast Northwest  \
CAUSE.CATEGORY                                                                 
equipment failure                7.65               7.92     12.35       6.9   
fuel supply emergency            7.44              10.51     16.03      7.29   
intentional attack               8.95               9.27     12.83      7.24   
islanding                        6.91              10.56     12.82      7.16   
public appeal                    9.49              10.61     13.09      5.71   
severe weather                   8.27               9.34     12.45      6.83   
system operability disruption     8.4               8.24     13.71      6.32   

CLIMATE.REGION                South Southeast Southwest   West  \
CAUSE.CATEGORY                                                   
equipment failure              8.24     10.15      8.07  12.74   
fuel supply emergency          9.17       NaN      8.65  13.82   
intentional attack             8.64      9.23      8.57  12.91   
islanding                      7.64       NaN      9.61  13.74   
public appeal                  8.41      8.34      7.73  12.89   
severe weather                 8.63      8.36      8.13  12.79   
system operability disruption  8.66      9.11      8.68  12.37   

CLIMATE.REGION                West North Central  
CAUSE.CATEGORY                                    
equipment failure                           6.21  
fuel supply emergency                        NaN  
intentional attack                          7.42  
islanding                                   7.84  
public appeal                               8.02  
severe weather                              6.37  
system operability disruption                NaN

## Step 3: Assessment of Missingness

### Part 3.1: Missingness Mechanism Analysis
If we look at our feature of interest, we can see that approximately 30 percent of values are missing. This is most likely not MCAR and requires more analysis to see if its missingness depends on other features.

In [562]:
raw_data[['CAUSE.CATEGORY.DETAIL']]

CAUSE.CATEGORY.DETAIL
1                           NaN
2                     vandalism
3                    heavy wind
4                  thunderstorm
5                           NaN
6                  winter storm
7                     tornadoes
8                  thunderstorm
9                      sabotage
10                    hailstorm
11                    hailstorm
12                    tornadoes
13                    vandalism
14                    vandalism
15                 thunderstorm
16            uncontrolled loss
17                    vandalism
18            uncontrolled loss
19                          NaN
20                          NaN
21                       winter
22                   wind storm
24                          NaN
25                       winter
26            computer hardware
27                          NaN
28                          NaN
29                 thunderstorm
30                          NaN
31                    vandalism
32                          NaN
33                    vandalism
34                       winter
35                 thunderstorm
36                          NaN
38                       winter
39                    vandalism
40                 winter storm
41                          NaN
42                        storm
43                   wind storm
44                       winter
45                          NaN
46                    vandalism
47                       winter
49                 winter storm
51                    vandalism
52                 thunderstorm
53                          NaN
54                         Coal
55                         Coal
56                 thunderstorm
57                    vandalism
58                     sabotage
59                        storm
60                          NaN
61                   heavy wind
62                    vandalism
63                    vandalism
64                         Coal
65                 thunderstorm
66                  Natural Gas
67                    vandalism
68                 thunderstorm
69                    vandalism
70                    vandalism
71                 thunderstorm
72                   hurricanes
73                 thunderstorm
74                          NaN
75                 thunderstorm
76                   heavy wind
77                          NaN
78                          NaN
79                        storm
80                          NaN
81                 winter storm
82                          NaN
83                          NaN
84                          NaN
85                 winter storm
86                 winter storm
87                 winter storm
88                          NaN
89                        storm
90                        storm
91                 thunderstorm
92                    wind/rain
93                 thunderstorm
94               snow/ice storm
95                 thunderstorm
96                 thunderstorm
97                 winter storm
98                    vandalism
99                    snow/ice 
100                thunderstorm
101                   wind/rain
102                thunderstorm
103                         NaN
104                         NaN
105                  heavy wind
106                thunderstorm
107                  heavy wind
108                         NaN
109   transmission interruption
110                thunderstorm
111                  heavy wind
112                winter storm
113                  heavy wind
114                         NaN
115                         NaN
116                   vandalism
117                winter storm
118                    flooding
119                   wind/rain
120                         NaN
121          transformer outage
122                thunderstorm
123                winter storm
124                         NaN
125                         NaN
126                thunderstorm
127                         NaN
128                         NaN
129       

In [563]:
raw_data['CAUSE.CATEGORY.DETAIL'].isna().mean()

np.float64(0.3035230352303523)

In [564]:
raw_data[['CAUSE.CATEGORY.DETAIL', 'CAUSE.CATEGORY']]

CAUSE.CATEGORY.DETAIL                 CAUSE.CATEGORY
1                           NaN                 severe weather
2                     vandalism             intentional attack
3                    heavy wind                 severe weather
4                  thunderstorm                 severe weather
5                           NaN                 severe weather
6                  winter storm                 severe weather
7                     tornadoes                 severe weather
8                  thunderstorm                 severe weather
9                      sabotage             intentional attack
10                    hailstorm                 severe weather
11                    hailstorm                 severe weather
12                    tornadoes                 severe weather
13                    vandalism             intentional attack
14                    vandalism             intentional attack
15                 thunderstorm                 severe weather
16            uncontrolled loss  system operability disruption
17                    vandalism             intentional attack
18            uncontrolled loss  system operability disruption
19                          NaN                 severe weather
20                          NaN                 severe weather
21                       winter                 severe weather
22                   wind storm                 severe weather
24                          NaN             intentional attack
25                       winter                 severe weather
26            computer hardware              equipment failure
27                          NaN                 severe weather
28                          NaN                 severe weather
29                 thunderstorm                 severe weather
30                          NaN                  public appeal
31                    vandalism             intentional attack
32                          NaN                 severe weather
33                    vandalism             intentional attack
34                       winter                 severe weather
35                 thunderstorm                 severe weather
36                          NaN                 severe weather
38                       winter                 severe weather
39                    vandalism             intentional attack
40                 winter storm                 severe weather
41                          NaN                 severe weather
42                        storm                 severe weather
43                   wind storm                 severe weather
44                       winter                 severe weather
45                          NaN              equipment failure
46                    vandalism             intentional attack
47                       winter                 severe weather
49                 winter storm                 severe weather
51                    vandalism             intentional attack
52                 thunderstorm                 severe weather
53                          NaN                 severe weather
54                         Coal          fuel supply emergency
55                         Coal          fuel supply emergency
56                 thunderstorm                 severe weather
57                    vandalism             intentional attack
58                     sabotage             intentional attack
59                        storm                 severe weather
60                          NaN                  public appeal
61                   heavy wind                 severe weather
62                    vandalism             intentional attack
63                    vandalism             intentional attack
64                         Coal          fuel supply emergency
65                 thunderstorm                 severe weather
66                  Natural Gas          fuel supply emergency
67                    vandalism          

In [565]:
''' This cell defines valid, relevant test statistics for permutation and 
hypothesis tests.
'''
def tvd(dist1: pd.Series, dist2: pd.Series):
    return (dist1.value_counts(normalize = True) - dist2.value_counts(normalize = True)).abs().sum() / 2

def ks(dist1: pd.Series, dist2: pd.Series):
    return scipy.stats.ks_2samp(dist1, dist2)

In [566]:
''' This function takes in a dataframe, a column with missing values and a 
column to analyze the type of missingness mechanism with. It will return
a p-value and an associative True or False indicating if missing_col is MAR 
withrespect to col. To conduct the permutation test, it will use the given 
test_stat.

The function will also graph the distribution of simulated test statistics 
with a line indicating where the observed lies.
'''
    
def identify_mar(df, missing_col, col, test_stat, N, alpha):
    missing_dist = df[[col]].assign(is_missing = df[missing_col].isna())
    observed = test_stat(missing_dist[missing_dist['is_missing']][col], missing_dist[~missing_dist['is_missing']][col])
    simulations = np.array([])
    for _ in range(N):
        missing_dist['is_missing'] = np.random.permutation(missing_dist['is_missing'])
        simulated = test_stat(missing_dist[missing_dist['is_missing']][col], missing_dist[~missing_dist['is_missing']][col])
        simulations = np.append(simulations, simulated)
    
    fig = px.histogram(x = simulations, title = f'Permutation Test Distribution', labels={'x': 'Simulated Test Statistics'}, histnorm = 'probability')
    fig.add_vline(x=observed, line_color='red', line_width=2, annotation_text='Observed', annotation_position='top right')
    fig.show()    
    
    p_value = (simulations > observed).mean()
    return p_value, p_value < alpha

In [567]:
p_val, is_mar = identify_mar(raw_data, 'CAUSE.CATEGORY.DETAIL', 'U.S._STATE', tvd, 1000, 0.05)
p_val, is_mar

(np.float64(0.0), np.True_)

In [568]:
p_val2, is_mar2 = identify_mar(raw_data, 'OUTAGE.DURATION', 'MONTH', tvd, 1000, 0.05)
p_val2, is_mar2

(np.float64(0.608), np.False_)

Clearly, the `CAUSE.CATEGORY.DETAIL_` column is **MAR** with respect to `CAUSE.CATEGORY_`. In other words, the missingness for cause category details are *highly* dependent on what the actual cause category is, which makes a lot of sense intuitively.

## Step 4: Hypothesis Testing

$H_0$: The proportion of each cause category is uniformly distributed across each season, for each cause category.

$H_a$: The proportion of each cause category is not uniformly distributed across each season, for each cause category.

In [569]:
''' Calculates the TVD for 2D distributions across each column (axis = 0). 
The resulting TVD's will be aggregated (sum or mean) to represent the TVD of 
the whole distributions. Assumes the probability distributions are already
calculated and provided.
'''
def tvd_2d(dist1: pd.DataFrame, dist2: pd.DataFrame, aggfunc):
    return (np.sum(np.abs(dist1 - dist2), axis = 0) / 2).agg(aggfunc)

In [570]:
seasonal_counts = raw_data.pivot_table(values = 'OBS', columns = 'SEASONAL.BINS', index = 'CAUSE.CATEGORY', aggfunc = 'size')

cause_totals = seasonal_counts.sum(axis = 0)
seasonal_totals = seasonal_counts.sum(axis = 1)
expected_proportions = seasonal_totals / seasonal_counts.sum().sum()

observed_dist = seasonal_counts / cause_totals
expected_dist = pd.DataFrame(data = {col: expected_proportions for col in observed_dist.columns})
observed_tvd = tvd_2d(expected_dist, observed_dist, 'sum')
observed_dist

SEASONAL.BINS                  Fall  Spring  Summer  Winter
CAUSE.CATEGORY                                             
equipment failure              0.02    0.05    0.05    0.03
fuel supply emergency          0.02    0.04    0.02    0.03
intentional attack             0.23    0.35    0.23    0.30
islanding                      0.03    0.03    0.04    0.02
public appeal                  0.06    0.02    0.07    0.02
severe weather                 0.57    0.40    0.51    0.53
system operability disruption  0.07    0.11    0.09    0.06

In [571]:
NUM_SIMULATIONS = 1000
sim_season_df = raw_data[['SEASONAL.BINS', 'CAUSE.CATEGORY', 'OBS']]
simulations = []
for _ in range(NUM_SIMULATIONS):
    sim_season_df['SEASONAL.BINS'] = np.random.permutation(sim_season_df['SEASONAL.BINS'])
    sim_counts = sim_season_df.pivot_table(values = 'OBS', columns = 'SEASONAL.BINS', index = 'CAUSE.CATEGORY', aggfunc = 'size')

    sim_cause_totals = sim_counts.sum(axis = 0)
    sim_seasonal_totals = sim_counts.sum(axis = 1)
    sim_expected_proportions = sim_seasonal_totals / sim_counts.sum().sum()

    sim_observed_dist = sim_counts / sim_cause_totals
    sim_expected_dist = pd.DataFrame(data = {col: sim_expected_proportions for col in sim_observed_dist.columns})
    sim_tvd = tvd_2d(sim_expected_dist, sim_observed_dist, 'sum')
    
    simulations.append(sim_tvd)
simulations

[np.float64(0.11738710444551893),
 np.float64(0.12331989636477558),
 np.float64(0.10590555675338789),
 np.float64(0.1750509678401592),
 np.float64(0.10982639976424069),
 np.float64(0.128656106048201),
 np.float64(0.13921177994407488),
 np.float64(0.11255076089574358),
 np.float64(0.17795937651590896),
 np.float64(0.13693987041385605),
 np.float64(0.13785550063907687),
 np.float64(0.13682048267567562),
 np.float64(0.10713448509381396),
 np.float64(0.14366526051953604),
 np.float64(0.20329231998744357),
 np.float64(0.13652886780035323),
 np.float64(0.12701579078643566),
 np.float64(0.10530673879264038),
 np.float64(0.1433147109515245),
 np.float64(0.20232841966227316),
 np.float64(0.10345012991212449),
 np.float64(0.18988305486390772),
 np.float64(0.09899530960103381),
 np.float64(0.14501961213914094),
 np.float64(0.09980055397376351),
 np.float64(0.11275934458990239),
 np.float64(0.10024100529387639),
 np.float64(0.08618897422792812),
 np.float64(0.11487342245117836),
 np.float64(0.1378

In [572]:
fig_hyp1 = px.histogram(simulations, histnorm = 'probability', title = 'Cause Category by Season Distribution of TVD')
fig_hyp1.add_vline(x=observed_tvd, line_color='red', line_width=2, annotation_text='Observed', annotation_position='top right')
fig_hyp1.show()

In [573]:
p_val_hyp1 = (observed_tvd < simulations).mean()
p_val_hyp1
np.array(simulations).mean(), np.array(simulations).std()

(np.float64(0.1431508193776529), np.float64(0.029407952597958427))

### Test Number 2

$H_0$: The distributions of mean affected customers for each state is the same for observations from 2000-2008 and 2008-2016.

$H_a$: The distributions of mean affected customers for each state is different for observations from 2000-2008 and 2008-2016.

In [574]:
raw_data['YEAR'] = raw_data['YEAR'].astype(float)
customers_dist_2005 = raw_data[raw_data['YEAR'] == 2005.0][['U.S._STATE', 'CUSTOMERS.AFFECTED']].groupby('U.S._STATE').mean()
customers_dist_2005 /= customers_dist_2005.sum(axis = 0)
customers_dist_2005 = customers_dist_2005['CUSTOMERS.AFFECTED'].dropna()

customers_dist_2006 = raw_data[raw_data['YEAR'] == 2006.0][['U.S._STATE', 'CUSTOMERS.AFFECTED']].groupby('U.S._STATE').mean()
customers_dist_2006 /= customers_dist_2006.sum(axis = 0)
customers_dist_2006 = customers_dist_2006['CUSTOMERS.AFFECTED'].dropna()

observed_tvd_customers = np.abs(customers_dist_2006 - customers_dist_2005).sum() / 2
observed_tvd_customers


np.float64(0.1931225644342009)

In [575]:
N_CUSTOMERS = 1000
sim_customers_2006 = np.random.multinomial(N_CUSTOMERS, pvals = customers_dist_2005, size = 100_000) / N_CUSTOMERS
sim_tvds_customers = np.sum(np.abs(sim_customers_2006 - customers_dist_2005.to_numpy()), axis = 1) / 2
px.histogram(sim_tvds_customers).add_vline(x=observed_tvd_customers, line_color='red', line_width=2, annotation_text='Observed', annotation_position='top right').show()
sim_tvds_customers.mean(), sim_tvds_customers.std()

(np.float64(0.04386220649403443), np.float64(0.009299661560213073))

In [576]:
p_val_hyp2 = (np.array(sim_tvds_customers) >= observed_tvd_customers).mean()
p_val_hyp2

np.float64(0.0)

## Step 5: Framing a Prediction Problem

We plan to predict the cause column, which represents the general cause of power outages. Since this column contains categorical data, it is a classification problem. We will use features such as the number of people affected, outage duration, demand loss, and climatic conditions to build a predictive model. We aim to uncover patterns that help identify the causes of power outages based on their associated impacts and conditions. This will provide valuable insights for improving outage management and preparedness.

## Step 6: Baseline Model

In [694]:
mdl_data = raw_data.drop(columns = ['CAUSE.CATEGORY.DETAIL', 'OUTAGE.START', 'OUTAGE.END', 'SEASONAL.BINS', 'NERC.REGION', 'OBS'])
mdl_data.isna().sum(axis = 0).sort_values(ascending=False)

DEMAND.LOSS.MW        672
CUSTOMERS.AFFECTED    622
OUTAGE.DURATION        78
TOTAL.PRICE            12
TOTAL.SALES            12
CLIMATE.REGION          5
CAUSE.CATEGORY          0
ANOMALY.LEVEL           0
U.S._STATE              0
MONTH                   0
YEAR                    0
CLIMATE.CATEGORY        0
TOTAL.CUSTOMERS         0
TOTAL.REALGSP           0
dtype: int64

In [695]:
mdl_data[['DEMAND.LOSS.MW', 'CUSTOMERS.AFFECTED', 'OUTAGE.DURATION']] = mdl_data[['DEMAND.LOSS.MW', 'CUSTOMERS.AFFECTED', 'OUTAGE.DURATION']].fillna(0)
mdl_data.dropna(subset = ['TOTAL.PRICE', 'TOTAL.SALES', 'CLIMATE.REGION'], inplace = True)

C:\Users\Kaii Bijlani\AppData\Local\Temp\ipykernel_73880\4038403078.py:1: FutureWarning:

Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`



In [696]:

mdl_base = Pipeline(steps = [
    ('data_encoding', ColumnTransformer(transformers = [
        ('one_hot', OneHotEncoder(handle_unknown = 'ignore'), ['U.S._STATE', 'CLIMATE.REGION', 'CLIMATE.CATEGORY']),
        ('ordinal', OrdinalEncoder(), ['MONTH']),
    ], remainder = 'passthrough')),
    ('random_forest', RandomForestClassifier())
])

In [697]:
X = mdl_data.drop(columns = ['CAUSE.CATEGORY'])
y = mdl_data['CAUSE.CATEGORY']
X_train, X_test, y_train, y_test = train_test_split(X, y)

mdl_data.isna().sum(axis = 0).sort_values(ascending=False)

YEAR                  0
MONTH                 0
U.S._STATE            0
CLIMATE.REGION        0
ANOMALY.LEVEL         0
CAUSE.CATEGORY        0
CLIMATE.CATEGORY      0
OUTAGE.DURATION       0
DEMAND.LOSS.MW        0
CUSTOMERS.AFFECTED    0
TOTAL.PRICE           0
TOTAL.SALES           0
TOTAL.CUSTOMERS       0
TOTAL.REALGSP         0
dtype: int64

In [698]:
mdl_base.fit(X_train, y_train)

c:\Users\Kaii Bijlani\.conda\envs\dsc80\Lib\site-packages\sklearn\compose\_column_transformer.py:1623: FutureWarning:


The format of the columns of the 'remainder' transformer in ColumnTransformer.transformers_ will change in version 1.7 to match the format of the other transformers.
At the moment the remainder columns are stored as indices (of type int). With the same ColumnTransformer configuration, in the future they will be stored as column names (of type str).
To use the new behavior now and suppress this warning, use ColumnTransformer(force_int_remainder_cols=False).




Pipeline(steps=[('data_encoding',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('one_hot',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  ['U.S._STATE',
                                                   'CLIMATE.REGION',
                                                   'CLIMATE.CATEGORY']),
                                                 ('ordinal', OrdinalEncoder(),
                                                  ['MONTH'])])),
                ('random_forest', RandomForestClassifier())])

In [699]:
mdl_base.score(X_train, y_train)

1.0

In [700]:
mdl_base.score(X_test, y_test), float(f1_score(y_test, mdl_base.predict(X_test), average = 'macro'))

(0.821917808219178, 0.5554021601788702)

## Step 7: Final Model

In [ ]:
# TODO

## Step 8: Fairness Analysis

In [ ]:
# TODO